In [ ]:
from os import listdir
from os.path import isfile, join
import os
import json
import zipfile
import re
import pkgutil
import os
import encodings

class AutoVivification(dict):
    """Implementation of perl's autovivification feature."""
    def __getitem__(self, item):
        try:
            return dict.__getitem__(self, item)
        except KeyError:
            value = self[item] = type(self)()
            return value

        
# Encodings function
def all_encodings():
    modnames = set(
        [modname for importer, modname, ispkg in pkgutil.walk_packages(
            path=[os.path.dirname(encodings.__file__)], prefix='')])
    aliases = set(encodings.aliases.aliases.values())
    return modnames.union(aliases)

# file_type function requirements

magic_dict = {
    "\x1f\x8b\x08": "gz",
    "\x42\x5a\x68": "bz2",
    "\x50\x4b\x03\x04": "zip"
    }

max_len = max(len(x) for x in magic_dict)

def file_type(filename_in):
    encodings = all_encodings()
    for enc in encodings:
        try:
            with open(filename_in, encoding=enc) as f_in:
                file_start = f_in.read(max_len)
        except:
            pass
    for magic, filetype in magic_dict.items():
        if file_start.startswith(magic):
            return filetype
    return "no match"

#os.walk(directory)
pcaps_dir='/home/cc/Contagio'
directories = [x[0] for x in os.walk(pcaps_dir)]
directories = [ x for x in directories if "MACOSX" not in x ]

#Variables
cnt_pcap=0
cnt_p=0
cnt_wrong_pwd=0
my_dict = AutoVivification()

for i_dir in range(1,len(directories)):
    print(directories[i_dir] + "\n")
    mypath = directories[i_dir]
    
    #onlyfiles = [f for f in listdir(mypath) if isfile(join(mypath, f)) and f.endswith('.zip') or f.endswith('.ZIP')]
    onlyfiles = [f for f in listdir(mypath) if isfile(join(mypath, f)) and file_type(mypath + "/" + f)=="zip"]
    non_compressed_files = [f for f in listdir(mypath) if isfile(join(mypath, f)) and file_type(mypath + "/" + f)=="no match"]
    #onlyfiles = [f for f in listdir(mypath) if isfile(join(mypath, f))]
    for file_x in onlyfiles:
        fullpath = mypath + "/" + file_x
        print(fullpath)
        print(file_type(fullpath))
        print("\n")
    if not os.path.exists(directories[i_dir] + "/unziped"):
        os.makedirs(directories[i_dir] + "/unziped")

    destination_dir = directories[i_dir] + "/unziped"
    for file in onlyfiles:
        print("\n"+ directories[i_dir] + "/" + file)
        path_to_zip_file = directories[i_dir] + "/" + file
        try:
            cnt_pcap=cnt_pcap+1
            zip_ref = zipfile.ZipFile(path_to_zip_file, 'r')
            zip_ref.extractall(destination_dir)
            zip_ref.close()
            print("Extraction Succesful")
            my_dict[directories[i_dir]]['Successful'][file]=None
            
        except:
            cnt_pcap=cnt_pcap-1
            print("Password Required")
            cnt_p=cnt_p+1
            try:
                zip_ref = zipfile.ZipFile(path_to_zip_file, 'r')
                zip_ref.extractall(destination_dir,None,pwd=b'infected666p')
                zip_ref.close()
                cnt_p=cnt_p-1
                cnt_pcap=cnt_pcap+1
                print("Extraction Succesful")
                my_dict[directories[i_dir]]['Successful'][file]=None
            except:
                cnt_wrong_pwd=cnt_wrong_pwd+1
                print("Invalid Password")
                my_dict[directories[i_dir]]['Pending'][file]=None
            
    onlyfiles=[]
    

print("\nFinal Results")
print("Successful Extractions: %s" %cnt_pcap)
print("Unsuccessful Extractions: %s" %cnt_p)
print("Invalid Passwords: %s" %cnt_wrong_pwd)
print("\nDictionary")
print(json.dumps(my_dict, sort_keys=True, indent=4))
print("\nCompressed files")
print(onlyfiles)
print("\nNon_compressed_files")
print(non_compressed_files)

In [ ]:
import pyshark
import os
from os.path import isfile, join
from os import listdir
from pprint import pprint
import re

def print_highest_layer(pkt):
    print (pkt.highest_layer)

def get_capture_count(pkt):
    count = []
    def counter(*args):
        count.append(args[0])
    pkt.apply_on_packets(counter, timeout=100000)
    return len(count)

def extract(dict_in, dict_out):
    for key, value in dict_in.iteritems():
        if isinstance(value, dict): # If value itself is dictionary
            extract(value, dict_out)
        elif isinstance(value, unicode):
            # Write to dict_out
            dict_out[key] = value
    return dict_out

#uncpx_pcaps_dir = []
'''
for key, value in my_dict.items():
    uncpx_pcaps_dir.append(key+"/unziped")
'''
pcaps_dir='/home/cc/Contagio'
directories = [x[0] for x in os.walk(pcaps_dir)]
directories = [ x for x in directories if "MACOSX" not in x and "unziped" in x]
#for dir in directories:
#    uncpx_pcaps_dir.append(dir+"/unziped")
    
print(directories)
uncpx_pcaps_dir = directories
eth_list = []
ip_list = []
udp_list = []
dns_list = []
tcp_list = []
icmp_list = []
http_list = []
data_list = []
media_list = []
png_list = []
json_list = []
image_list = []
failed_pcaps=[]
pkt_layers_full=[]

ip_output_dict = {}

for pcap_dir in uncpx_pcaps_dir[0:1]: #uncpx_pcaps_dir[0:1]
    print("\n")
    #print(pcap_dir)
    pcap_dir_files = [f for f in listdir(pcap_dir) if isfile(join(pcap_dir, f))]
    #print(pcap_dir_files)
    #print("\n")
    #pcap_dir_files = ["EK_MALWARE_2015-01-08-pcap-files-associated-with-malware-from-82.244.160.22_mailware-traffic-analysis.net.zip"]
    pcap_dir_files = ["EK_MALWARE_2014-03-09-callback-traffic-from-physical-host_mailware-traffic-analysis.net.pcap"]
    for i_cap in pcap_dir_files:
        cap = pyshark.FileCapture(pcap_dir+'/'+i_cap, keep_packets=True)
        print("Current PCAP:")
        print(pcap_dir+'/'+i_cap)
        try:
            print("Capture Count:")
            print(get_capture_count(cap))
            print("\n")
            #print("\n PCAP Highest Layer:")
            #print_highest_layer(cap[0])

            pkt_num = 0
            for i_pkt in cap:
                #print("\n *** PKT: %s ***" %pkt_num)
                i_pkt_layers = []
                i_pkt_layers = re.findall(r'<(\w+)', str(i_pkt.layers))
                #print(i_pkt_layers)
                for i_layer in i_pkt_layers:
                    pkt_layers_full.append(i_layer)
                pkt_num = pkt_num+1
                
                if i_pkt_layers:
                    #pprint(type(i_pkt.eth))
                    #pprint(type(i_pkt.eth._all_fields))
                    #print(i_pkt.eth._all_fields)
                    #print("Pretty Print")
                    #pprint(i_pkt.eth._all_fields)
                    try:
                        #print("--- ETH LAYER ---")
                        pprint(i_pkt.eth._all_fields)
                        #pprint(i_pkt.eth._all_fields.keys())
                        #for key in i_pkt.eth._all_fields.keys():
                        #    eth_list.append(key)
                    except:
                        pass
                    try:
                        #print("--- IP LAYER ---")
                        #print('\nAllFields\n')
                        #print(type(pprint(i_pkt.ip._all_fields)))
                        pprint(i_pkt.ip._all_fields)
                        #pprint(i_pkt.ip._all_fields.keys())
                        #for key in i_pkt.ip._all_fields.keys():
                        #    ip_list.append(key)
                        #print('\nExtracted Dict\n')
                        #extract(i_pkt.ip._all_fields,ip_output_dict)
                        #pprint(ip_output_dict)
                    except:
                        pass
                    try:
                        #print("--- UDP LAYER ---")
                        pprint(i_pkt.udp._all_fields)
                        #pprint(i_pkt.udp._all_fields.keys())
                        #for key in i_pkt.udp._all_fields.keys():
                        #    udp_list.append(key)
                    except:
                        pass
                    try:
                        #print("--- DNS LAYER ---")
                        pprint(i_pkt.dns._all_fields)
                        #pprint(i_pkt.dns._all_fields.keys())
                        #for key in i_pkt.dns._all_fields.keys():
                        #    dns_list.append(key)
                    except:
                        pass
                    try:
                        #print("--- TCP LAYER ---")
                        pprint(i_pkt.tcp._all_fields)
                        #pprint(i_pkt.tcp._all_fields.keys())
                        #for key in i_pkt.tcp._all_fields.keys():
                        #    tcp_list.append(key)
                    except:
                        pass
                    try:
                        #print("--- ICMP LAYER ---")
                        pprint(i_pkt.icmp._all_fields)
                        #pprint(i_pkt.icmp._all_fields.keys())
                        #for key in i_pkt.icmp._all_fields.keys():
                        #    icmp_list.append(key)
                    except:
                        pass
                    try:
                        #print("--- HTTP LAYER ---")
                        pprint(i_pkt.http._all_fields)
                        #for key in i_pkt.http._all_fields.keys():
                        #    http_list.append(key)
                    except:
                        pass
                    try:
                        #print("--- DATA LAYER ---")
                        pprint(i_pkt.data._all_fields)
                        #for key in i_pkt.data._all_fields.keys():
                        #    data_list.append(key)
                    except:
                        pass
                    try:
                        #print("--- MEDIA LAYER ---")
                        pprint(i_pkt.media._all_fields)
                        #for key in i_pkt.media._all_fields.keys():
                        #    media_list.append(key)
                    except:
                        pass
                    try:
                        #print("--- PNG LAYER ---")
                        pprint(i_pkt.png._all_fields)
                        #for key in i_pkt.png._all_fields.keys():
                        #    png_list.append(key)
                    except:
                        pass
                    try:
                        #print("--- JSON LAYER ---")
                        pprint(i_pkt.json._all_fields)
                        #for key in i_pkt.json._all_fields.keys():
                        #    json_list.append(key)
                    except:
                        pass
                    try:
                        #print("--- IMAGE LAYER ---")
                        pprint(i_pkt.json._all_fields)
                        #for key in i_pkt.image._all_fields.keys():
                        #    image_list.append(key)
                    except:
                        pass
            
        except:
            failed_pcaps.append(pcap_dir+'/'+i_cap)
            print("\n")
            pass

# Get unique values
eth_set = list(set(eth_list))
ip_set = list(set(ip_list))
udp_set = list(set(udp_list))
dns_set = list(set(dns_list))
tcp_set = list(set(tcp_list))
icmp_set = list(set(icmp_list))
http_set = list(set(http_list))
data_set = list(set(data_list))
media_set = list(set(media_list))
png_set = list(set(png_list))
json_set = list(set(json_list))
image_set = list(set(image_list))
pkt_layers_full_set = list(set(pkt_layers_full))

print("ETH Set")
print(eth_set)
print("IP Set")
print(ip_set)
print("UDP Set")
print(udp_set)
print("DNS Set")
print(dns_set)
print("TCP Set")
print(tcp_set)
print("ICMP SET")
print(icmp_set)
print("HTTP Set")
print(http_set)
print("DATA Set")
print(data_set)
print("MEDIA Set")
print(media_set)
print("PNG Set")
print(png_set)
print("JSON Set")
print(json_set)
print("IMAGE Set")
print(image_set)
print("Layers")
print(pkt_layers_full_set)
print("\nFailed PCAPS")
print(failed_pcaps)
'''
with open("Results.txt", "w") as output:
    output.write(" ETH Features")
    output.write(str(eth_set))
    output.write("\n\n IP Features")
    output.write(str(ip_set))
    output.write("\n\n UDP Features")
    output.write(str(udp_set))
    output.write("\n\n DNS Features")
    output.write(str(dns_set))
    output.write("\n\n TCP Features")
    output.write(str(tcp_set))
    output.write("\n\n ICMP Features")
    output.write(str(icmp_set))
    output.write("\n\n HTTP Features")
    output.write(str(http_set))
    output.write("\n\n DATA Features")
    output.write(str(data_set))
    output.write("\n\n MEDIA Features")
    output.write(str(media_set))
    output.write("\n\n PNG Features")
    output.write(str(png_set))
    output.write("\n\n JSON Features")
    output.write(str(json_set))
    output.write("\n\n IMAGE Features")
    output.write(str(image_set))
    output.write("\n\n Layers")
    output.write(str(pkt_layers_full_set))
    output.write("\n\n Failed PCAPS")
    output.write(str(failed_pcaps))
output.close()
'''

['/home/cc/Contagio/Exploit_Kits_and_Malware/unziped', '/home/cc/Contagio/Exploits_and_Scans/unziped', '/home/cc/Contagio/APT/unziped', '/home/cc/Contagio/GENERAL_DEFCON_17/unziped', '/home/cc/Contagio/General/unziped', '/home/cc/Contagio/CRIME/unziped', '/home/cc/Contagio/CRIME/unziped/tbotpcaps']


Current PCAP:
/home/cc/Contagio/Exploit_Kits_and_Malware/unziped/EK_MALWARE_2014-03-09-callback-traffic-from-physical-host_mailware-traffic-analysis.net.pcap
Capture Count:
4079


{'eth.addr': '58:6d:8f:b0:f7:4e',
 'eth.addr_resolved': '58:6d:8f:b0:f7:4e',
 'eth.dst': '58:6d:8f:b0:f7:4e',
 'eth.dst_resolved': '58:6d:8f:b0:f7:4e',
 'eth.ig': '0',
 'eth.lg': '0',
 'eth.src': '00:1b:21:ca:fe:d7',
 'eth.src_resolved': '00:1b:21:ca:fe:d7',
 'eth.type': '0x00000800'}
{'': 'Source GeoIP: Unknown',
 'ip.addr': '192.168.1.104',
 'ip.checksum': '0x000077e1',
 'ip.checksum.status': '2',
 'ip.dsfield': '0x00000000',
 'ip.dsfield.dscp': '0',
 'ip.dsfield.ecn': '0',
 'ip.dst': '209.18.47.61',
 'ip.dst_h

In [ ]:
#PYSHARK PARSER
import pyshark_parser
from pyshark_parser import packet_util
from pyshark_parser import layer_util
from pyshark_parser import pcap_util

print(dir(pyshark_parser.pcap_util))
print(pyshark_parser.pcap_util.aggregate_layer(cap))


In [ ]:
#SCAPY
import scapy
print(dir(scapy))
data = pcap_dir+'/'+pcap_dir_files[1]
a = rdpcap(data)
sessions = a.sessions()
i = 1
for session in sessions:
    http_payload = ""
    for packet in sessions[session]:
        print(packet)